In [6]:
import pandas as pd
from Bio import SeqIO
from collections import Counter, defaultdict
import pprint
import json
import numpy as np
from collections import Counter
import shutil
import os
from collections import defaultdict
import requests

%load_ext autoreload
%autoreload 1
%aimport functions

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [7]:
analysis_folder = 'data/analysis/'

In [8]:
H37Rv_results = pd.read_csv(analysis_folder + '/H37Rv_combined.csv',sep='\t')
# Identify columns that contain "ICDS" in their name
fs_cols = [col for col in H37Rv_results.columns if "ICDS" in col]

# Include the "BLASTP" column in the list of columns to select
selected_cols = fs_cols + ["Reference entries mapped - all strains", "ORF ids - all strains"] + ['Identifier']

# Select the desired columns from the DataFrames
fs = H37Rv_results#[selected_cols]


# Function to patch the 'Reference ICDS evidence' column
# patch for a known bug causing ICDS for another strain to be reported if the current strain did not yield a reference ICDS
def clean_reference_icds(series, exclude_str):
    """
    Cleans the 'Reference ICDS evidence' column by removing entries containing the exclude string.
    """
    return series.apply(lambda x: None if exclude_str in str(x) else x)

# Apply the patch to the 'Reference ICDS evidence' column
fs['Reference ICDS evidence'] = clean_reference_icds(fs['Reference ICDS evidence'], exclude_str="_MYCTO")

# Function to preprocess the DataFrame
def preprocess_fs(df, icds_cols):
    """
    Preprocesses the DataFrame by:
    - Dropping rows where all ICDS columns are NaN
    - Removing duplicate rows
    - Resetting the index
    """
    df = df.dropna(subset=icds_cols, how='all')  # Drop rows where all "ICDS" columns are NaN
    df = df.drop_duplicates()                   # Remove duplicate rows
    df = df.reset_index(drop=True)              # Reset the index
    return df

# Preprocess the DataFrames
fs = preprocess_fs(fs, fs_cols)
interstrain_icds_all =  fs[(fs['Strain ICDS intrastrain evidence S5527'].notnull()) | (fs['Strain ICDS intrastrain evidence S507'].notnull()) ] 

interstrain_icds_all['icds'] = '+'
#print(interstrain_icds)
#interstrain_icds = interstrain_icds.reset_index()
##del interstrain_icds['index']
##icds_proteins = []
for x in interstrain_icds_all['Reference BLAST - all strains'].tolist():
    for xx in x.split('\n'):
        print(xx)
interstrain_icds = interstrain_icds_all[['id', "icds"]]
interstrain_icds

P96901
P96202
Q79FP0
O53158
I6YGC8
P9WQ51
O07738


<ipython-input-8-c4b6221cb58b>:40: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  interstrain_icds_all['icds'] = '+'


id icds
2    410    +
8   1079    +
12  2354    +
13  2357    +
14  2362    +

In [9]:
#interstrain_icds_all.columns.tolist()

In [10]:
acetyl_differences = pd.read_csv(analysis_folder + 'annotations/export/H37Rv/Combined_Proteins_Nterm_Acetylation_Differences.csv')
del acetyl_differences['Unnamed: 0']
acetyl_differences = acetyl_differences.sort_values(['Strains'])
acetyl_differences = acetyl_differences.reset_index()
del acetyl_differences['index']
acetyl_differences

BLASTP Strains Gene Name  \
0   P9WMS7    S507      guaA   
1   P9WQD9    S507      kasA   
2   P9WLT1    S507    Rv1708   
3   P71922    S507   Rv2426c   
4   P9WK15    S507      mbtK   
5   O69727    S507    fadE36   
6   P9WIH3    S507      pckG   
7   O53842    S507   Rv0831c   
8   O50398    S507    Rv3369   
9   I6XCB2    S507      scpB   
10  P9WN95    S507      ftsZ   
11  P9WP71   S5527      ctaD   
12  P9WMK7   S5527      hupB   
13  P9WP79   S5527      fbiB   
14  P9WKI1   S5527      ino1   
15  P9WK87   S5527      nlhH   
16  I6X8D2   S5527     pks13   
17  P9WGX7   S5527      rsbW   
18  P9WGY5   S5527      rpoZ   
19  P96878   S5527    Rv3273   
20  P96404   S5527     echA1   
21  P96389   S5527   Rv0207c   
22  P71658   S5527      mihF   
23  O65934   S5527    Rv1747   
24  O07717   S5527     aceAb   
25  O06154   S5527   Rv1637c   
26  P9WHQ9   S5527       hpt   
27  Q79FJ2   S5527      gnd1   

                                         Protein Name  
0                GMP synthase [glutamine-hydrolyzing]  
1         3-oxoacyl-[acyl-carrier-protein] synthase 1  
2                      Uncharacterized protein Rv1708  
3               AAA+ ATPase domain-containing protein  
4                       Lysine N-acyltransferase MbtK  
5              Possible acyl-CoA dehydrogenase FadE36  
6             Phosphoenolpyruvate carboxykinase [GTP]  
7                                   Conserved protein  
8                                   Conserved protein  
9   Possible segregation and condensation protein ...  
10                         Cell division protein FtsZ  
11            Probable cytochrome c oxidase subunit 1  
12                           DNA-binding protein HupB  
13        Bifunctional F420 biosynthesis protein FbiB  
14                      Inositol-3-phosphate synthase  
15                              Carboxylesterase NlhH  
16                          Polyketide synthase Pks13  
17                           Anti-sigma-F factor RsbW  
18          DNA-directed RNA polymerase subunit omega  
19                                 carbonic anhydrase  
20  Probable enoyl-CoA hydratase EchA1 (Enoyl hydr...  
21                      NYN domain-containing protein  
22                            Integration host factor  
23  ABC transporter ATP-binding/permease protein R...  
24                Putative isocitrate lyase subunit B  
25                                  Conserved protein  
26     Hypoxanthine-guanine phosphoribosyltransferase  
27  6-phosphogluconate dehydrogenase, decarboxylating

In [11]:
import Bio
from Bio import SeqIO

s507_fasta = list(SeqIO.parse('data/analysis/annotations/H37Rv_S507_variants.fasta', 'fasta'))
s5527_fasta = list(SeqIO.parse('data/analysis/annotations/H37Rv_S5527_variants.fasta', 'fasta'))
combined_fasta = s507_fasta + s5527_fasta

# Create a dictionary to store the sequences
sequences = {}
for record in combined_fasta:
    sequences[record.id] = str(record.seq)
    
def fix_var_lengths(df):
    """
    Fixes the 'VarLength' column by calculating the length of the variant sequence. Explicitly 
    creates a CorrectedVarLength column. The VarLength column is removed if it exists.
    The VarLength column includes ORF stop codons in the amino acid sequence, which is not
    desirable for the analysis. This will be fixed in a future release.
    """

    # calculate the length of the variant sequence for rows where VarId is not NaN
    df['CorrectedVarLength'] = df['VarId'].apply(lambda x: len(sequences[x]) if pd.notnull(x) else None)

    try:
        del df['VarLength']
    except:
        pass
    return df

In [12]:
exclusive_tss = pd.read_csv(analysis_folder + 'annotations/H37Rv_exclusive_tss.csv')

# apply the patch for the var length column
exclusive_tss = fix_var_lengths(exclusive_tss)

#tss_diff = pd.read_csv(analysis_folder +'/annotations/export/H37Rv/Combined_Proteins_TSS_Differences.csv')
#del tss_diff['Unnamed: 0']
#exclusive_tss= pd.merge(exclusive_tss, tss_diff, left_on='BLASTP', right_on='BLASTP')
exclusive_tss = exclusive_tss.sort_values(['BLASTP'])
filt = exclusive_tss[exclusive_tss['BLASTP'] == 'I6X8D2']
tss_cols = [i for i in exclusive_tss.columns if i.startswith('Identified ')] + ['BLASTP','CorrectedVarLength','PeptideSequence','VarId']
acetyl_filt_cols = [i for i in filt.columns if i.startswith('Acetylated ')] + ['BLASTP','PeptideSequence']
exclusive_tss.head()
exclusive_tss = exclusive_tss[tss_cols].drop_duplicates()
exclusive_tss.head()



Identified S507_ST  Identified S5527_ST  Identified S5527_MLexp  \
232                True                False                   False   
156                True                False                   False   
130               False                False                    True   
196               False                False                   False   
205               False                False                   False   

     Identified S507_ML  Identified S507_MLexp  Identified S5527_ML  BLASTP  \
232               False                  False                False  I6X5C9   
156               False                  False                False  I6X630   
130               False                  False                 True  I6X8D2   
196                True                   True                False  I6X9S5   
205               False                   True                False  I6XCB2   

     CorrectedVarLength                PeptideSequence  \
232                 170             VSEHHSNETVTFSSTYIR   
156                 109           MWLPFRWPGSQGVTVTEDGR   
130                1733                 ADVAESQENAPAER   
196                 407                       ELHARFGR   
205                 231  TEHMPEHDPSYGIPDIAEPAELDADELKR   

                                                 VarId  
232  S507_scaffold8_size205631|S507_scaffold8_size2...  
156  S507_scaffold17_size99894|S507_scaffold17_size...  
130  S5527_scaffold9_size227503|S5527_scaffold9_siz...  
196  S507_scaffold31_size42200|S507_scaffold31_size...  
205  S507_scaffold3_size242019|S507_scaffold3_size2...

In [13]:
s5527_peptide_annotations_groups = pd.read_csv(analysis_folder + '/annotations/H37Rv_S5527_peptide_annotations_groups.csv')
s507_peptide_annotations_groups = pd.read_csv(analysis_folder + '/annotations/H37Rv_S507_peptide_annotations_groups.csv')




combined_peptide_annotations = pd.concat([s5527_peptide_annotations_groups, s507_peptide_annotations_groups])

# apply the patch for the var length column
combined_peptide_annotations = fix_var_lengths(combined_peptide_annotations)



acetyl_cols = [i for i in combined_peptide_annotations.columns if i.startswith('Acetylated ')]
identified_cols = [i for i in combined_peptide_annotations.columns if i.startswith('Identified')]

# Subset the columns of interest

subset = combined_peptide_annotations[acetyl_cols]
subset2 = combined_peptide_annotations[identified_cols]

# For each row, check how many unique values it has
combined_peptide_annotations['Acetylation_Differences'] = (subset.nunique(axis=1) != 1)
combined_peptide_annotations['Identification_Differences'] = (subset2.nunique(axis=1) != 1)

combined_peptide_annotations = combined_peptide_annotations.sort_values("BLASTP")


acetyl_sample_differences = combined_peptide_annotations[combined_peptide_annotations['Acetylation_Differences'] == True]
tss_differences = combined_peptide_annotations[(combined_peptide_annotations['Identification_Differences'] == True)]
tss_differences = tss_differences[tss_differences['VarId'].notnull()]



# exclude peptides that are not acetylated in any strain
#acetyl_sample_any = combined_peptide_annotations[~(combined_peptide_annotations[acetyl_cols] == False).all(axis=1)].drop_duplicates(acetyl_filt_cols)
filt_cols = ['CorrectedVarLength','PeptidePosition'] + identified_cols + acetyl_filt_cols

tss_sample_any = combined_peptide_annotations[(combined_peptide_annotations['VarId'].notnull())].drop_duplicates(acetyl_filt_cols + identified_cols)

pep2blast = combined_peptide_annotations.set_index('PeptideSequence')['BLASTP'].to_dict()
#.drop_duplicates(acetyl_filt_cols + identified_cols)


acetyl_sample_any = combined_peptide_annotations[~(combined_peptide_annotations[acetyl_cols] == False).all(axis=1)].drop_duplicates(acetyl_filt_cols + identified_cols)


#combined_peptide_annotations.head()


acetyl_sample_any[filt_cols]

CorrectedVarLength  PeptidePosition  Identified S507_ST  \
26452               139.0                5                True   
1582                 53.0                4                True   
2862                103.0               16                True   
708                1733.0                3               False   
25800               231.0                6               False   
...                   ...              ...                 ...   
34469               416.0                5                True   
34559               473.0               11                True   
11000               483.0               48                True   
20868               377.0               47                True   
32790               287.0               39                True   

       Identified S5527_ST  Identified S5527_MLexp  Identified S507_ML  \
26452                 True                    True                True   
1582                  True                    True                True   
2862                  True                   False                True   
708                  False                    True               False   
25800                False                   False               False   
...                    ...                     ...                 ...   
34469                 True                    True                True   
34559                 True                    True                True   
11000                 True                    True                True   
20868                 True                    True                True   
32790                 True                    True                True   

       Identified S507_MLexp  Identified S5527_ML  Acetylated S507_ST  \
26452                   True                 True                True   
1582                    True                 True                True   
2862                    True                 True               False   
708                    False                 True               False   
25800                   True                False               False   
...                      ...                  ...                 ...   
34469                   True                 True               False   
34559                   True                 True                True   
11000                   True                 True               False   
20868                   True                 True                True   
32790                   True                 True               False   

       Acetylated S5527_ST  Acetylated S5527_MLexp  Acetylated S507_ML  \
26452                False                    True                True   
1582                 False                    True                True   
2862                 False                   False               False   
708                  False                    True               False   
25800                False                   False               False   
...                    ...                     ...                 ...   
34469                False                   False                True   
34559                 True                    True                True   
11000                 True                   False               False   
20868                 True                    True                True   
32790                 True                    True                True   

       Acetylated S507_MLexp  Acetylated S5527_ML  BLASTP  \
26452                  False                 True  I6WZD7   
1582                    True                 True  I6X824   
2862                    True                 True  I6X849   
708                    False                 True  I6X8D2   
25800                   True                False  I6XCB2   
...                      ...                  ...     ...   
34469                  False                False  P9WQD9   
34559                   True                 True  P9WQH5   
11000     

In [14]:
acetyl_sample_any[filt_cols].head()

CorrectedVarLength  PeptidePosition  Identified S507_ST  \
26452               139.0                5                True   
1582                 53.0                4                True   
2862                103.0               16                True   
708                1733.0                3               False   
25800               231.0                6               False   

       Identified S5527_ST  Identified S5527_MLexp  Identified S507_ML  \
26452                 True                    True                True   
1582                  True                    True                True   
2862                  True                   False                True   
708                  False                    True               False   
25800                False                   False               False   

       Identified S507_MLexp  Identified S5527_ML  Acetylated S507_ST  \
26452                   True                 True                True   
1582                    True                 True                True   
2862                    True                 True               False   
708                    False                 True               False   
25800                   True                False               False   

       Acetylated S5527_ST  Acetylated S5527_MLexp  Acetylated S507_ML  \
26452                False                    True                True   
1582                 False                    True                True   
2862                 False                   False               False   
708                  False                    True               False   
25800                False                   False               False   

       Acetylated S507_MLexp  Acetylated S5527_ML  BLASTP  \
26452                  False                 True  I6WZD7   
1582                    True                 True  I6X824   
2862                    True                 True  I6X849   
708                    False                 True  I6X8D2   
25800                   True                False  I6XCB2   

                     PeptideSequence  
26452              TQTTQSPALIASQSSWR  
1582             TQPTAWEYATVPLLTHATK  
2862                SETSETPTPPPHQTPK  
708                   ADVAESQENAPAER  
25800  TEHMPEHDPSYGIPDIAEPAELDADELKR

In [15]:
gsea_path='data/analysis/gsea'
diff_path='data/analysis/diff'
print(os.listdir(gsea_path))

['go_terms.csv', 'kotermset.Rdata', 'ipr_target_proteins.tsv', 'koterm2proteingroups.csv', 'ec_terms.csv', 'iprset.Rdata', 'accession2reactome.p', 'ccset.Rdata', 'metacyc2proteingroups.csv', 'custom', 'kopathwayset.Rdata', 'accession2ec.p', 'combined.csv', 'ecset.Rdata', 'ec2proteingroups.csv', 'metacyc_terms.csv', 'reactome_terms.csv', 'reactomeset.Rdata', 'ipr_terms.csv', 'accession2metacyc.p', 'reactome2proteingroups.csv', 'mfset.Rdata', 'ipr2proteingroups.csv', 'bpset.Rdata', 'StrainCondition', 'accession2go.p', 'host.csv', 'metacycset.Rdata', 'accession2ipr.p', 'kopathway2proteingroups.csv', 'go2proteingroups.csv', 'kegg2proteingroups.csv', 'keggset.Rdata', 'other.csv']


In [16]:
with open("All-pathways-of-M.-tuberculosis-H37Rv.txt") as f:
    allowed_metacyc = f.read().split()
#print(allowed_metacyc)

In [17]:
class summarize_functional_analysis:
    def __init__(self, gsea_path, diff_path):
        self.gsea_path=gsea_path
        self.diff_path = diff_path
        self.diff_prots = defaultdict()
        self.diff_ko = defaultdict()
        
        self.norm=pd.read_csv(self.diff_path + '/protein_normalization/msnbase/normalized.csv')
        #print(self.norm.id)
        #print(self.norm.head())
        #print(self.norm.columns.tolist())
        
        self.annotation2protein=defaultdict(set)
        self.protein2annnotation=defaultdict(set)

        self.norm = pd.merge(self.norm, interstrain_icds, how='outer')
        self.icds_norm = self.norm[self.norm['icds'] == '+']
        self.icds = set(self.norm[self.norm['icds'] == '+']['Identifier'].tolist())
        #print(self.norm[self.norm['icds'] == '+'])
        
        self.norm.apply(self.load_graph, axis=1)
        
        self.id2blast = self.norm.set_index('Identifier')['Leading.Protein'].to_dict()

        #print(self.id2blast)
        #print(self.annotation2protein)
        
        for file in os.listdir(self.gsea_path + '/custom/'):
            if file.endswith('2proteingroups.csv'):
                mapping = pd.read_csv(self.gsea_path+ '/custom/' + file)
                for row in mapping.iterrows():
                    annotation = row[1]['ID']
                    genes = row[1]['GENES']
                    for gene in genes.split('|'):
                         self.annotation2protein[annotation].add(gene)
                        
        
    def load_graph(self, df):
        #self.df['Identifier'])
        
        def load_terms(term, df):
            try:
                terms =  df[term].split(';')
                for i in terms:
                    self.annotation2protein[i].add(df['Identifier'])
            except:
                pass

        

        load_terms('X_ipr.term.union', df)
        load_terms('X_go.term.union', df)
        load_terms('X_reactome.term.union', df)
        load_terms('X_metacyc.term.union', df)
        load_terms('Leading.Protein.Kegg.Orthology', df)
        load_terms('Leading.Protein.Kegg.Pathways', df)
       

    def get_kegg_pathway_name(self, pathway_id):
        url = f"http://rest.kegg.jp/get/{pathway_id}"
        response = requests.get(url)
        if response.status_code == 200:
            lines = response.text.split('\n')
            for line in lines:
                if line.startswith("NAME"):
                    return line.split("NAME")[1].strip()
        return None

        # Example usage
        #pathway_id = 'mtu01120'
        #pathway_name = get_kegg_pathway_name(pathway_id)
        #print(f"Pathway ID: {pathway_id}, Pathway Name: {pathway_name}")      
            
    def summarize(self):
        protein_diff_folder = self.diff_path+'/StrainCondition/protein_diff/limma/'
        peptide_diff_folder = self.diff_path+'/StrainCondition/peptide_diff/limma/'
        ko_diff_folder = self.diff_path+'/StrainCondition/Leading.Protein.Kegg.Orthology/limma/'
     
        pathways_seen = []
        annotations_seen = []
        combined_res = []

        diff_prots_list = []
        diff_kos_list = []
        diff_peptide_list = []

        
        for file in os.listdir(protein_diff_folder):
            suff = '_intensity_qval_0.05.csv'
            if file.endswith(suff):
                condition = file.split('limma_')[1].split(suff)[0]
                condition_name = '_'.join(condition.split('-'))
                
                print(condition_name)
                
                diff_prots = pd.read_csv(protein_diff_folder + '/' + file)
                #print(diff_prots)                
                
                diff_ko = pd.read_csv(ko_diff_folder + '/' + file)

                diff_peptide = pd.read_csv(peptide_diff_folder + '/' + file)
               
                
                diff_prots = diff_prots[['Row.names','Leading.Protein','logFC','AveExpr','P.Value', 'adj.P.Val']]
                diff_ko = diff_ko[['Row.names','logFC','AveExpr','P.Value', 'adj.P.Val']]
                diff_peptide = diff_peptide[['Row.names','logFC','AveExpr','P.Value', 'adj.P.Val']]

                diff_ko['Comparison'] = condition
                diff_kos_list.append(diff_ko)
                
                diff_prots['Comparison'] = condition
                diff_prots_list.append(diff_prots)

                diff_peptide['Comparison'] = condition
                diff_peptide_list.append(diff_peptide)
                
                #if len(diff_prots) > 0:
                #    print(diff_prots)
                #    _ = diff_prots['Row.names'].tolist()
                #    for n in _:
                #        print(self.norm[self.norm['Identifier'] == n])
                
                #print(diff_prots)
                self.diff_prots[condition_name] = diff_prots
                self.diff_ko[condition_name] = diff_ko
                
                gsea_dir = self.gsea_path + '/StrainCondition/' + condition_name
                res  = []

                # find out if intra strain differences are common or different between strains - leave out commoun from graph
                #def get_difference(df, strains=['S5527','S507']):
                #    temp_df = df.copy()
                #    temp_df['Exposed_Strain'] = temp_df['Exposed'].apply(lambda x : x.split('_')[0])
                #    temp_df['Control_Strain'] = temp_df['Control'].apply(lambda x : x.split('_')[0])#

                #    temp_df['Exposed_Cond'] = temp_df['Exposed'].apply(lambda x : x.split('_')[1])
                #    temp_df['Control_Cond'] = temp_df['Control'].apply(lambda x : x.split('_')[1])

                #    temp_df['CompGroup'] = temp_df['Exposed_Cond'] + ' ' + temp_df['Control_Cond'] + ' ' +  temp_df['Coregulated']

                #    duplicated_rows = temp_df[temp_df['CompGroup'].duplicated(keep=False)] 


                for gs in os.listdir(gsea_dir):
                    
                    if gs.endswith('.combined.csv'):
                        source =gs.split('.')[0]
                        #if gs.startswith("KEGG."):
                        #print(gs)
                        gs_df = pd.read_csv(gsea_dir + '/' + gs)
                        gs_df = gs_df[['p.geomean', 'stat.mean', 'p.val',     'q.val',  'set.size','Exposed',  'Control',   'RowName','Coregulated']]

                        gs_df['source'] = source

                        if source == "METACYC":
                            gs_df = gs_df[gs_df['RowName'].apply(lambda  x : x in allowed_metacyc )] 
                        res.append(gs_df)

                for gs in os.listdir(gsea_dir + '/custom/'):
                    
                    if gs.endswith('.combined.csv'):
                        source =gs.split('.')[0]
                        #if gs.startswith("KEGG."):
                        #print(gs)
                        gs_df = pd.read_csv(gsea_dir + '/custom/' + gs)
                        gs_df = gs_df[['p.geomean', 'stat.mean', 'p.val',     'q.val',  'set.size','Exposed',  'Control',   'RowName','Coregulated']]

                        gs_df['source'] = source
                                              
                        res.append(gs_df)
                        
                res_df = pd.concat(res)
                combined_res.append(res_df)

                
                kegg_df = res_df[res_df['source'] == "KEGG"]     
                pathways = list(set(kegg_df['RowName'].tolist()))

                sig_res = res_df[res_df['q.val'] < 0.25]
                annotations = list(set(sig_res['RowName'].tolist()))
                pathways_seen += pathways
                annotations_seen += annotations
                print()

        self.diff_prots_combined = pd.concat(diff_prots_list)
        self.diff_kos_combined = pd.concat(diff_kos_list)
        self.diff_peptides_combined = pd.concat(diff_peptide_list)

        self.diff_peptides_combined['BLASTP'] = self.diff_peptides_combined['Row.names'].map(pep2blast)

        self.diff_peptides_combined = self.diff_peptides_combined.sort_values("BLASTP")
       
        self.pathways_counted = Counter(pathways_seen)
        # Get items from highest count to lowest
        self.sorted_pathways= self.pathways_counted.most_common()

        self.annotations_counted = Counter(annotations_seen)
        # Get items from highest count to lowest
        self.sorted_annotations= self.annotations_counted.most_common()
        
        combined_res_df = pd.concat(combined_res)
        self.combined_res_df = combined_res_df

        self.pathway_graph = defaultdict(set)
        self.pathway_weight = defaultdict(int)
        
        # function to make q-value to 3 significant terms 
        def fix_qvalue(qval):
            if qval < 0.001:
                return "{:.3e}".format(qval)
            else:
                return "{:.3f}".format(qval)

        self.diff_kos_combined['adj.P.Val'] = self.diff_kos_combined['adj.P.Val'].apply(fix_qvalue)
        self.diff_prots_combined['adj.P.Val'] = self.diff_prots_combined['adj.P.Val'].apply(fix_qvalue)
        self.diff_peptides_combined['adj.P.Val'] = self.diff_peptides_combined['adj.P.Val'].apply(fix_qvalue)      
        self.sig_res = self.combined_res_df[self.combined_res_df['q.val'] < 0.25]
        self.combined_res_df['q.val'] = self.combined_res_df['q.val'].apply(fix_qvalue)

        self.sig_res['q.val'] = self.sig_res['q.val'].apply(fix_qvalue)

        
        self.diff_prots_combined['logFC'] = self.diff_prots_combined['logFC'].apply(fix_qvalue)
        self.diff_peptides_combined['logFC'] = self.diff_peptides_combined['logFC'].apply(fix_qvalue)
        self.diff_kos_combined['logFC'] = self.diff_kos_combined['logFC'].apply(fix_qvalue)


        #for annotation, group in self.sig_res.groupby('RowName'):
        #    print(annotation)
        #    print(self.annotations_counted[annotation])
        #    print(group)
        #    break
        #return

        kegg_summary = pd.DataFrame()
        
        for pathway, count in self.sorted_pathways:
            if not pathway.startswith('mtu'):
                continue
            assert not pathway == 'mtu02020'
            print("***")
            kegg_name = self.get_kegg_pathway_name(pathway)

            
            print(pathway, kegg_name, count)
            print()
            _ = combined_res_df[combined_res_df['RowName']==pathway]

            set_size = _['set.size'].values[0]
            
            print("Set size: " , set_size)
            del _['set.size']
            del _['RowName']
            del _['p.geomean']
            del _['source']
            
            print(_)

            kegg_summary.loc[pathway, 'Kegg Name'] = kegg_name   
            kegg_summary.loc[pathway, 'Set Size'] = set_size  
            #kegg_summary.loc[pathway, 'Differences'] = int(count)


            cond_comps = defaultdict(list)
            for row in _.iterrows():
                coregulated = row[1]['Coregulated']
                exposed =row[1]['Exposed']
                control = row[1]['Control']
                comparison = exposed + ' vs ' + control
                qvalue = row[1]['q.val']
                message = coregulated + ' (q-value {})'.format(str(qvalue))
                cond_comps[comparison].append(message)

            
            for comp in cond_comps:
                kegg_summary.loc[pathway, comp] = '; '.join(cond_comps[comp])
                #kegg_summary.loc[pathway, comparison] = message
            #kegg_summary.loc[pathway, 'ICDS'] = len(self.annotation2protein[pathway] & self.icds)

            #del _['p.geomean']
            pathway_prots = self.annotation2protein[pathway]
            
            for rowname in self.sig_res['RowName'].unique():
                newrowname = rowname
                if rowname.startswith("GO:"):
                    newrowname = rowname.split()[0]
                    
                intersect_prots = pathway_prots & self.annotation2protein[newrowname]
                
                
                if len(intersect_prots) > 0:
                    self.pathway_graph[pathway].add(rowname)
                    self.pathway_weight[pathway] += 1
                    #print(pathway)
                    #assert not rowname.startswith("MT3978-MT3989")
                  
            for rowname in self.diff_prots_combined['Row.names'].unique():
                if rowname in pathway_prots:
                     self.pathway_graph[pathway].add(rowname)
            for rowname in self.diff_kos_combined['Row.names'].unique():
                if len(self.annotation2protein[rowname] & pathway_prots) > 0:
                    self.pathway_graph[pathway].add(rowname)
            
        kegg_summary['Set Size'] = kegg_summary['Set Size'].astype(int)
        #kegg_summary['Differences'] = kegg_summary['Differences'].astype(int)
        #print(kegg_summary)
        self.kegg_summary = kegg_summary

    def describe(self, pathway):
        children = self.pathway_graph[pathway]
        pathway_prots = self.annotation2protein[pathway]

        pathway_icds = pathway_prots & self.icds
        print("* Pathway ICDS: ", pathway_icds)

        blast_proteins = [self.id2blast[x] for x in pathway_prots]
        #print(blast_proteins)

        exlusive_tss_sample_prots = tss_differences[tss_differences['BLASTP'].apply(lambda x : x in blast_proteins)]
        exlusive_tss_prots = exclusive_tss[exclusive_tss['BLASTP'].apply(lambda x : x in blast_proteins)]

        acetyl_sample_diff_prots = acetyl_sample_differences[acetyl_sample_differences['BLASTP'].apply(lambda x : x in blast_proteins)]
        acetyl_diff_prots = acetyl_differences[acetyl_differences['BLASTP'].apply(lambda x : x in blast_proteins)]

        differences = set()
        
        #print("* TSS Sample Peptide Isoforms identified: ")
        _ = exlusive_tss_sample_prots['BLASTP'].unique()
        #print(_)
        #differences.update(set(_))
        
        print("* TSS Strain Isoforms identified: ")
        _ = exlusive_tss_prots['BLASTP'].unique()
        print(_)
        differences.update(set(_))

        #print("* Acetylation sample peptide differences identified: ")
        _ = acetyl_sample_diff_prots['BLASTP'].unique()
        #print(_)
        #differences.update(set(_))

        
        print("* Acetylation strain differences identified: ")
        _ = acetyl_diff_prots['BLASTP'].unique()
        print(_)
        differences.update(set(_))
        
        
        print(self.pathway_weight[pathway])
        prots_filt = self.diff_prots_combined[self.diff_prots_combined['Row.names'].apply(lambda x : x in pathway_prots)]
        kos_filt = self.diff_kos_combined[self.diff_kos_combined['Row.names'].apply(lambda x : x in children)]
        peps_filt = self.diff_peptides_combined[self.diff_peptides_combined['BLASTP'].apply( lambda x : x in blast_proteins)]
        
        
        kos_terms = kos_filt['Row.names'].tolist()
        kos_proteins  = set()
        for ko in kos_terms:
            prots = self.annotation2protein[ko]
            for t in prots:
                kos_proteins.add(self.id2blast[t])
        #differences.update(kos_proteins)
        
        exlusive_tss_kos = exclusive_tss[exclusive_tss['BLASTP'].apply(lambda x : x in kos_proteins)]
        acetyl_sample_diff_kos = acetyl_sample_differences[acetyl_sample_differences['BLASTP'].apply(lambda x : x in kos_proteins)]
        acetyl_diff_kos = acetyl_differences[acetyl_differences['BLASTP'].apply(lambda x : x in kos_proteins)]
        
        print("* Differential peptides")
        _ = peps_filt.BLASTP.unique()
        print(_)
        #differences.update(set(_))
        print(peps_filt)

        print("* Differential TSS peptides")
        tss_blastp = tss_sample_any['BLASTP'].unique()

        try:
            print(peps_filt[peps_filt['BLASTP'].apply(lambda x : x in tss_blastp)]['BLASTP'].unique())
        except:
            pass
        
        
        print("* Differential Proteins")
        print("** Exclusive TSS diff prots: ", set(prots_filt['Leading.Protein']) & set(exlusive_tss_prots['BLASTP']))
        print("** Acetylation sample peptide diff prots: ", set(prots_filt['Leading.Protein']) & set(acetyl_sample_diff_prots['BLASTP']))
        print("** Acetylation diff prots: ", set(prots_filt['Leading.Protein']) & set(acetyl_diff_prots['BLASTP']))

        _ = set(prots_filt['Leading.Protein'].unique())
        #differences.update(_)
        
        print(prots_filt)

        print("* Differential KOs")
        print("** Exclusive TSS diff kos: ", set(exlusive_tss_kos['BLASTP']))
        print("** Acetylation sample peptide diff kos: ", set(acetyl_sample_diff_kos['BLASTP']))
        print("** Acetylation diff kos: ", set(acetyl_diff_kos['BLASTP']))

        print(kos_filt)

        pathway_filt = self.sig_res[self.sig_res['RowName'].apply(lambda x : x in children)]
        pathway_filt['count'] = pathway_filt['RowName'].map(self.annotations_counted)
        pathway_filt = pathway_filt.sort_values(['count','RowName'], ascending = False)
        for name, group in pathway_filt.groupby('source'):
            print(name)
            #assert not name.startswith("operons")
            sorted_group = group.sort_values(['count', 'RowName'], ascending=False)
            for term in sorted_group['RowName'].unique():
                print("***")
                print(term)
                
                #del sorted_group['RowName']
                newterm = term
                if newterm.startswith("GO:"):
                    newterm = term.split()[0]
                    
                term_prots = self.annotation2protein[newterm]
                #print("Term prots", term_prots)
                term_blast = [self.id2blast[x] for x in term_prots if x in self.id2blast]
                filt_relevant = set(term_blast) & differences
                print(filt_relevant)
                
                term_group = sorted_group[sorted_group['RowName'] == term].copy()
                del term_group['RowName']
               
                count = term_group['count'].values[0]
                
                print(count)
                del term_group['count']
                print(term_group) 
            
summary= summarize_functional_analysis(gsea_path, diff_path)
summary.summarize()

S507_ST_S507_ML

S5527_ML_S507_ML

S5527_ST_S507_ST

S5527_MLexp_S507_MLexp

S5527_ST_S5527_ML

S507_MLexp_S507_ML

S5527_MLexp_S5527_ML

***


<ipython-input-17-59ddddb3ab55>:220: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.sig_res['q.val'] = self.sig_res['q.val'].apply(fix_qvalue)


mtu03010 Ribosome - Mycobacterium tuberculosis H37Rv 6

Set size:  46
   stat.mean         p.val      q.val      Exposed     Control Coregulated
0  -3.780185  2.647689e-07  2.065e-05      S507_ST     S507_ML        Down
0   1.250767  4.363498e-02      1.000      S507_ST     S507_ML        Both
0   1.194089  2.457835e-02      0.994     S5527_ML     S507_ML          Up
0   2.654116  1.741124e-04      0.014     S5527_ST     S507_ST          Up
1   1.741845  7.784393e-03      0.304  S5527_MLexp  S507_MLexp          Up
0  -2.128838  1.672151e-03      0.073     S5527_ST    S5527_ML        Down
3  -1.256566  1.711481e-02      0.334   S507_MLexp     S507_ML        Down
***
mtu05152 Tuberculosis - Mycobacterium tuberculosis H37Rv 5

Set size:  25
   stat.mean     p.val  q.val      Exposed     Control Coregulated
1  -1.610818  0.014785  0.554      S507_ST     S507_ML        Down
0   1.309746  0.034112  1.000     S5527_ST     S507_ST        Both
0   1.909526  0.004646  0.362  S5527_MLexp  S507_ML

## ICDS analysis

In [18]:
def df_diff(df, term):
    for row in df.iterrows():
        #print(list(row[1].index))
        print("Proteins: ", row[1]['ORF.Proteins'])

        #children = self.pathway_graph[pathway]
        #pathway_prots = self.annotation2protein[pathway]
        #pathway_icds = pathway_prots & self.icds
        #print("* Pathway ICDS: ", pathway_icds)
        #blast_proteins = [self.id2blast[x] for x in pathway_prots]
        
        m = row[1][term]
        
      
        metacyc = []
        #m = df[term].tolist()
        linked = set()
        temp = summary.sig_res.copy()
        temp = temp[temp['q.val'].astype("float64") < 0.05]
        names = summary.sig_res['RowName'].unique()
        #for _ in m:
        try:
            _ = str(m)
        except:
            continue

        
        for __ in str(m).split(';'):
            
            if term == 'X_metacyc.term.union':
                if __ in allowed_metacyc and __ in names:
                    linked.add(__)
            else:
                if __ in names:
                    linked.add(__)
        print(linked)
        #for p in linked:
        #    print(p)
        #    term_prots = summary.annotation2protein[p]
            #print(term_prots)
        #    mapped_kegg = []
        #    for pp in term_prots:
        #        break
        pathways = []
        for pathway in summary.pathway_graph.keys():
            if not pathway in names:
                continue
            pathway_children = summary.pathway_graph[pathway]
            matches = len(list(pathway_children & linked))
            if matches > 0:
                pathways.append(pathway)
                
        #print(Counter(pathways))
            
        print()
df_diff(summary.icds_norm, 'X_metacyc.term.union')


Proteins:  P96901
{'PWY-7221', 'PWY-7909', 'PWY-7220', 'PWY-6613', 'PWY-7206', 'PWY-7197', 'PWY-7226', 'PWY-7884', 'PWY-6383', 'PWY-7210', 'PWY-6545', 'PWY-2161', 'PWY-6147', 'PWY-1722', 'PWY-5340', 'PWY-7187', 'PWY-6163', 'PWY-7219', 'PWY-7781', 'PWY-6164', 'PWY-7227', 'PWY-7184', 'PWY-7222', 'PWY-7176', 'PWY-7181', 'PWY-7250', 'PWY-7205'}

Proteins:  P96202
{'PWY-7346', 'PWY-7221', 'PWY-7909', 'PWY-7220', 'PWY-6613', 'PWY-3341', 'PWY-7180', 'PWY-7197', 'PWY-6113', 'PWY-7226', 'PWY-6580', 'PWY-2301', 'PWY-5188', 'PWY-7210', 'PWY-6545', 'PWY-5194', 'PWY-5041', 'PWY-5989', 'PWY-2161', 'PWY-4381', 'PWY-1722', 'PWY-5667', 'PWY-7686', 'PWY-5366', 'PWY-5512', 'PWY-7187', 'PWY-7744', 'PWY-6163', 'PWY-7219', 'PWY-6969', 'PWY-6164', 'PWY-6317', 'PWY-7227', 'PWY-7184', 'PWY-6614', 'PWY-7222', 'PWY-7176', 'PWY-7181', 'PWY-5971', 'PWY-7344', 'PWY-7205'}

Proteins:  O53158;Q79FP0
{'PWY-7895'}

Proteins:  P9WQ51
{'PWY-5989', 'PWY-5837', 'PWY-5971'}

Proteins:  O07738
{'PWY-5989', 'PWY-5366', 'PWY-4

In [19]:
summary.sig_res[summary.sig_res['RowName'] == 'PWY-6113']

p.geomean  stat.mean     p.val  q.val  set.size      Exposed     Control  \
118   0.031888  -1.576420  0.013239  0.185       220  S5527_MLexp  S507_MLexp   
395   0.021400   1.957852  0.002902  0.013       220     S5527_ST    S5527_ML   
557   0.073042   1.447467  0.006174  0.020       220   S507_MLexp     S507_ML   

      RowName Coregulated   source  
118  PWY-6113        Down  METACYC  
395  PWY-6113          Up  METACYC  
557  PWY-6113          Up  METACYC

In [20]:
#summary.icds_norm.columns.tolist()

In [21]:
df_diff(summary.icds_norm, 'Leading.Protein.Kegg.Pathways')


Proteins:  P96901
set()

Proteins:  P96202
set()

Proteins:  O53158;Q79FP0
set()

Proteins:  P9WQ51
set()

Proteins:  O07738
set()



## 3.2 Differential abundance

In [23]:
from collections import Counter
import pprint
print(len(summary.diff_prots_combined))
print(len(summary.diff_kos_combined))
print(len(summary.diff_peptides_combined))

comparison_differences = Counter(summary.diff_prots_combined['Comparison'])

# convert the dict of comparison differnces to a pandas dataframe,
comparison_differences_df = pd.DataFrame.from_dict(comparison_differences, orient='index').reset_index()
print(comparison_differences_df)

summary.diff_prots_combined.to_excel('supplementary/s1.xlsx')
summary.diff_kos_combined.to_excel('supplementary/s2.xlsx')
summary.diff_peptides_combined.to_excel('supplementary/s3.xlsx')

summary.diff_prots_combined.head()

133
109
274
                    index    0
0         S507_ST-S507_ML    2
1        S5527_ST-S507_ST    2
2  S5527_MLexp-S507_MLexp    1
3       S5527_ST-S5527_ML  126
4    S5527_MLexp-S5527_ML    2


Row.names Leading.Protein       logFC    AveExpr  \
0  O53480 (Protein group 1523)          O53480  -6.520e+00  20.050497   
1  P9WH65 (Protein group 1569)          P9WH65  -1.514e+00  25.711435   
0  P9WKY9 (Protein group 1318)          P9WKY9  -3.758e+00  19.341564   
1  O06404 (Protein group 1920)          O06404  -5.006e+00  18.837614   
0  I6X9V3 (Protein group 1608)          I6X9V3       2.037  21.415833   

        P.Value  adj.P.Val              Comparison  
0  8.312852e-08  1.777e-04         S507_ST-S507_ML  
1  2.578639e-05      0.028         S507_ST-S507_ML  
0  1.668969e-05      0.036        S5527_ST-S507_ST  
1  3.608474e-05      0.039        S5527_ST-S507_ST  
0  1.207084e-05      0.026  S5527_MLexp-S507_MLexp

In [24]:
# get proteins that are upregulated in S507_ST-S507_ML that  are not in S5527_ST-S5527_ML

def get_difference(df, strains=['S5527','S507']):
    temp_df = df.copy()
    temp_df['Exposed_Strain'] = temp_df['Comparison'].apply(lambda x : x.split('-')[0].split('_')[0])
    temp_df['Control_Strain'] = temp_df['Comparison'].apply(lambda x : x.split('-')[1].split('_')[0])

    temp_df['Exposed_Cond'] = temp_df['Comparison'].apply(lambda x : x.split('-')[0].split('_')[1])
    temp_df['Control_Cond'] = temp_df['Comparison'].apply(lambda x : x.split('-')[1].split('_')[1])

    temp_df['CompGroup'] = temp_df['Exposed_Cond'] + ' ' + temp_df['Control_Cond'] + ' ' +  temp_df['Leading.Protein']

    duplicated_rows = temp_df[temp_df['CompGroup'].duplicated(keep=False)] 
    return duplicated_rows
non_unique_diff = get_difference(summary.diff_prots_combined)
non_unique_diff

Row.names Leading.Protein       logFC    AveExpr  \
0   O53480 (Protein group 1523)          O53480  -6.520e+00  20.050497   
1   P9WH65 (Protein group 1569)          P9WH65  -1.514e+00  25.711435   
0   O53480 (Protein group 1523)          O53480  -6.263e+00  20.050497   
29  P9WH65 (Protein group 1569)          P9WH65  -1.170e+00  25.711435   

         P.Value  adj.P.Val         Comparison Exposed_Strain Control_Strain  \
0   8.312852e-08  1.777e-04    S507_ST-S507_ML           S507           S507   
1   2.578639e-05      0.028    S507_ST-S507_ML           S507           S507   
0   1.258778e-07  2.691e-04  S5527_ST-S5527_ML          S5527          S5527   
29  2.396731e-04      0.017  S5527_ST-S5527_ML          S5527          S5527   

   Exposed_Cond Control_Cond     CompGroup  
0            ST           ML  ST ML O53480  
1            ST           ML  ST ML P9WH65  
0            ST           ML  ST ML O53480  
29           ST           ML  ST ML P9WH65

In [25]:
diff_df = summary.diff_prots_combined

# compare MLexp between the  strains
print("MLexp Phase comparison")
print(diff_df[diff_df['Comparison'] == 'S5527_MLexp-S507_MLexp'])

MLexp Phase comparison
                     Row.names Leading.Protein  logFC    AveExpr   P.Value  \
0  I6X9V3 (Protein group 1608)          I6X9V3  2.037  21.415833  0.000012   

  adj.P.Val              Comparison  
0     0.026  S5527_MLexp-S507_MLexp  


In [26]:
# compare ST between the  strains
print("ST Phase comparison")
print(diff_df[diff_df['Comparison'] == 'S5527_ST-S507_ST'])

ST Phase comparison
                     Row.names Leading.Protein       logFC    AveExpr  \
0  P9WKY9 (Protein group 1318)          P9WKY9  -3.758e+00  19.341564   
1  O06404 (Protein group 1920)          O06404  -5.006e+00  18.837614   

    P.Value adj.P.Val        Comparison  
0  0.000017     0.036  S5527_ST-S507_ST  
1  0.000036     0.039  S5527_ST-S507_ST  


In [27]:
# compare MLexp vs ML hypervirulent
print("ST Phase comparison")
print(diff_df[diff_df['Comparison'] == 'S5527_MLexp-S5527_ML'])

ST Phase comparison
                     Row.names Leading.Protein       logFC    AveExpr  \
0  I6X9V3 (Protein group 1608)          I6X9V3       3.043  21.415833   
1   P9WJ21 (Protein group 578)          P9WJ21  -4.397e+00  18.656183   

        P.Value  adj.P.Val            Comparison  
0  2.337481e-07  4.998e-04  S5527_MLexp-S5527_ML  
1  3.836118e-05      0.041  S5527_MLexp-S5527_ML  


In [28]:
# lets make a function to print out all the functional information for a specific protein

def describe_prot(blast):
    res = summary.norm[summary.norm['Leading.Protein'] == blast]
    return res[res.columns[180:]]
describe_prot('P9WKY9')

Mygene.entrez Leading.Protein.Kegg.Orthology.ID  \
1178  887499;45427408                               NaN   

     Leading.Protein.Kegg.Orthology.Name Leading.Protein.Kegg.Pathways  \
1178                                 NaN                           NaN   

     Leading.Protein.KO.Pathways Leading.Protein.KO.Entrez  \
1178                         NaN                       NaN   

     Leading.Protein.Kegg.Orthology Component X_go.term.union  \
1178                            NaN      host             NaN   

      X_ec.term.union X_reactome.term.union X_metacyc.term.union  \
1178              NaN                   NaN                  NaN   

                                    X_ipr.term.union icds  
1178  IPR035165: Protein of unknown function DUF5319  NaN

## 3.3 Generally applicable gene enrichment (GAGE) 

In [29]:
print("Distinct terms qith q-value less than 0.05:")
for name, group in summary.sig_res.groupby('source'):
    #if name == 'KOPATHWAY':
    #    continue
    values  = group['RowName'].unique()
    print(name, len(values))

summary.sig_res.to_excel('supplementary/s4.xlsx')

Distinct terms qith q-value less than 0.05:
BP 9
CC 9
IPR 61
KEGG 48
KOPATHWAY 48
METACYC 66
MF 27
REACTOME 3015
operons_AllOperons2proteingroups 5


## 3.4 Pathway integration 

## Secondary metabolidate biosynthesis (mtu01110)

In [ ]:
summary.describe('mtu01110')
# 'IPR006091: Acyl-CoA oxidase/dehydrogenase, middle domain;IPR000084: PE-PGRS family, N-terminal;IPR009100: Acyl-CoA dehydrogenase/oxidase, N-terminal and middle domain superfamily;IPR009075: Acyl-CoA dehydrogenase/oxidase, C-terminal;IPR048996: PGRS repeats;IPR036250: Acyl-CoA dehydrogenase-like, C-terminal;IPR025878: Acetyl-CoA dehydrogenase-like C-terminal domain;IPR052166: Diverse substrate specificity acyl-CoA dehydrogenase;IPR020953: Acyl-CoA dehydrogenase, N-terminal, bacteria'

IPR013149: Alcohol dehydrogenase-like, C-terminal
set()
1
    p.geomean  stat.mean     p.val  q.val  set.size   Exposed   Control  \
16   0.084386    1.41874  0.026315  0.188        15  S5527_ST  S5527_ML   

   Coregulated source  
16          Up    IPR  
***
IPR009081: Phosphopantetheine binding ACP domain
{'I6X8D2'}
1
   p.geomean  stat.mean    p.val  q.val  set.size     Exposed  Control  \
4   0.041248   1.534339  0.00527  0.067        24  S507_MLexp  S507_ML   

  Coregulated source  
4          Up    IPR  
***
IPR008927: 6-phosphogluconate dehydrogenase-like, C-terminal domain superfamily
{'O53872', 'Q79FJ2'}
1
    p.geomean  stat.mean     p.val  q.val  set.size   Exposed   Control  \
11   0.053695   1.685943  0.012404  0.132        12  S5527_ST  S5527_ML   

   Coregulated source  
11          Up    IPR  
***
IPR006094: FAD linked oxidase, N-terminal
{'Q11061'}
1
    p.geomean  stat.mean     p.val  q.val  set.size   Exposed   Control  \
18     0.0917   1.391969  0.030919  0.188 

In [ ]:
summary.describe('mtu01120') # microbial metabolism in diverse environments

    p.geomean  stat.mean     p.val  q.val  set.size   Exposed   Control  \
18   0.109142   1.257039  0.042469  0.167        17   S507_ST   S507_ML   
25   0.078858   1.442710  0.023965  0.072        17  S5527_ST  S5527_ML   

   Coregulated source  
18          Up   KEGG  
25          Up   KEGG  
***
mtu00640
{'P96890', 'O53872', 'O53166', 'O07717'}
2
    p.geomean  stat.mean     p.val  q.val  set.size   Exposed   Control  \
2    0.090215  -1.336367  0.011534  0.227        28  S5527_ML   S507_ML   
11   0.032619   1.879930  0.004784  0.030        28  S5527_ST  S5527_ML   

   Coregulated source  
2         Down   KEGG  
11          Up   KEGG  
***
mtu00230
{'P9WKE3'}
2
    p.geomean  stat.mean     p.val  q.val  set.size      Exposed     Control  \
17   0.095007  -1.219989  0.044156  0.189        47  S5527_MLexp  S507_MLexp   
16   0.040443   1.732487  0.007878  0.035        47     S5527_ST    S5527_ML   

   Coregulated source  
17        Down   KEGG  
16          Up   KEGG  
***
mtu00

## Tuberculosis - Mycobacterium tuberculosis H37Rv (mtu05152)

In [ ]:
summary.describe('mtu05152')


set()
2
     p.geomean  stat.mean     p.val     q.val  set.size     Exposed  Control  \
102   0.042231   1.539863  0.014913  0.180871       316    S5527_ST  S507_ST   
221   0.024277   1.719043  0.001497  0.058769       316  S507_MLexp  S507_ML   

    Coregulated    source  
102          Up  REACTOME  
221          Up  REACTOME  
***
R-MMU-2559586
set()
2
     p.geomean  stat.mean     p.val     q.val  set.size     Exposed  Control  \
827   0.093813   1.236039  0.040484  0.180871       271    S5527_ST  S507_ST   
458   0.053741   1.447378  0.006194  0.109547       271  S507_MLexp  S507_ML   

    Coregulated    source  
827          Up  REACTOME  
458          Up  REACTOME  
***
R-MMU-171319
set()
2
     p.geomean  stat.mean     p.val     q.val  set.size     Exposed  Control  \
119   0.060316   1.510827  0.016511  0.180871       219    S5527_ST  S507_ST   
620   0.057835   1.386038  0.008351  0.117042       219  S507_MLexp  S507_ML   

    Coregulated    source  
119          Up  REAC

In [ ]:
# protein P9WNK5 (ESAT-6-like protein EsxB)
protein='P9WNK5'
peptide_filt= summary.diff_peptides_combined[summary.diff_peptides_combined['BLASTP'] == protein]['Row.names'].unique()
tss_filt= tss_sample_any[tss_sample_any['BLASTP'] == protein]['PeptideSequence'].unique()
combined_filt = list(tss_filt)+ list(peptide_filt)
combined_peptide_annotations[combined_peptide_annotations['PeptideSequence'].apply(lambda x : x in combined_filt) ][filt_cols].drop_duplicates()

In [ ]:
# protein P9WNK5 (ESAT-6-like protein EsxB)
protein='P9WNK5'
peptide_filt= summary.diff_peptides_combined[summary.diff_peptides_combined['BLASTP'] == protein]['Row.names'].unique()
tss_filt= tss_sample_any[tss_sample_any['BLASTP'] == protein]['PeptideSequence'].unique()
combined_filt = list(tss_filt)+ list(peptide_filt)
combined_peptide_annotations[combined_peptide_annotations['PeptideSequence'].apply(lambda x : x in combined_filt) ][filt_cols].drop_duplicates()

## Ribosome - Mycobacterium tuberculosis H37Rv (mtu03010)

In [ ]:
summary.describe("mtu03010")

In [ ]:
# TSS isoforms 'P9WH39' 'P9WH51' 'P9WHD3'
protein='P9WH39'
peptide_filt= summary.diff_peptides_combined[summary.diff_peptides_combined['BLASTP'] == protein]['Row.names'].unique()
tss_filt= tss_sample_any[tss_sample_any['BLASTP'] == protein]['PeptideSequence'].unique()
combined_filt = list(tss_filt)+ list(peptide_filt)
combined_peptide_annotations[combined_peptide_annotations['PeptideSequence'].apply(lambda x : x in combined_filt) ][filt_cols].drop_duplicates()

In [ ]:
protein='P9WH51'
peptide_filt= summary.diff_peptides_combined[summary.diff_peptides_combined['BLASTP'] == protein]['Row.names'].unique()
tss_filt= tss_sample_any[tss_sample_any['BLASTP'] == protein]['PeptideSequence'].unique()
combined_filt = list(tss_filt)+ list(peptide_filt)
combined_peptide_annotations[combined_peptide_annotations['PeptideSequence'].apply(lambda x : x in combined_filt) ][filt_cols].drop_duplicates()

In [ ]:
protein='P9WHD3'
peptide_filt= summary.diff_peptides_combined[summary.diff_peptides_combined['BLASTP'] == protein]['Row.names'].unique()
tss_filt= tss_sample_any[tss_sample_any['BLASTP'] == protein]['PeptideSequence'].unique()
combined_filt = list(tss_filt)+ list(peptide_filt)
combined_peptide_annotations[combined_peptide_annotations['PeptideSequence'].apply(lambda x : x in combined_filt) ][filt_cols].drop_duplicates()

## DNA Repair (mtu03430)

In [ ]:
summary.describe('mtu03430')

     p.geomean  stat.mean     p.val     q.val  set.size     Exposed   Control  \
8     0.028475   1.766498  0.006356  0.180871       319    S5527_ST   S507_ST   
160   0.012054   2.231672  0.000823  0.038042       319    S5527_ST  S5527_ML   
185   0.028148   1.781652  0.001043  0.048877       319  S507_MLexp   S507_ML   

    Coregulated    source  
8            Up  REACTOME  
160          Up  REACTOME  
185          Up  REACTOME  
***
R-MMU-193368
set()
3
     p.geomean  stat.mean     p.val     q.val  set.size     Exposed   Control  \
381   0.073864   1.336914  0.029493  0.180871       436    S5527_ST   S507_ST   
586   0.050449   1.604712  0.011706  0.173848       436    S5527_ST  S5527_ML   
2     0.002825   2.642796  0.000003  0.007341       436  S507_MLexp   S507_ML   

    Coregulated    source  
381          Up  REACTOME  
586          Up  REACTOME  
2            Up  REACTOME  
***
R-MMU-1660661
set()
3
     p.geomean  stat.mean     p.val     q.val  set.size     Exposed   Contr

In [ ]:
# XseB, Exodeoxyribonuclease 7 small subunit) 

protein='P9WF29'
peptide_filt= summary.diff_peptides_combined[summary.diff_peptides_combined['BLASTP'] == protein]['Row.names'].unique()
tss_filt= tss_sample_any[tss_sample_any['BLASTP'] == protein]['PeptideSequence'].unique()
combined_filt = list(tss_filt)+ list(peptide_filt)
combined_peptide_annotations[combined_peptide_annotations['BLASTP']==protein ][filt_cols].drop_duplicates()

## 3.4.3 Amino Acid Metabolism

In [ ]:

#summary.describe("mtu01230")

#summary.describe("mtu00270")
# https://www.uniprot.org/uniprotkb/O53390/entry
# https://www.uniprot.org/uniprotkb/P9WGV3/entry
# https://www.uniprot.org/uniprotkb/P9WP51/entry

#summary.describe("mtu00250")
# https://www.uniprot.org/uniprotkb/P9WN37/entry
# https://www.uniprot.org/uniprotkb/O53203/entry

#summary.describe("mtu00400")
# https://www.uniprot.org/uniprotkb/O53512/entry
# https://www.uniprot.org/uniprotkb/P9WFY1/entry

summary.describe("mtu00220")
# https://www.uniprot.org/uniprotkb/O53203/entry
# https://www.uniprot.org/uniprotkb/P9WN37/entry


R-SSC-1482798
{'O53203'}
3
      p.geomean  stat.mean     p.val     q.val  set.size     Exposed  \
2028   0.082205   1.176978  0.048848  0.180871       154    S5527_ST   
115    0.007602   2.431733  0.000316  0.022407       154    S5527_ST   
396    0.060732   1.506411  0.004678  0.101700       154  S507_MLexp   

       Control Coregulated    source  
2028   S507_ST          Up  REACTOME  
115   S5527_ML          Up  REACTOME  
396    S507_ML          Up  REACTOME  
***
R-SPO-9837999
{'O53203'}
3
     p.geomean  stat.mean     p.val     q.val  set.size     Exposed   Control  \
195   0.054886   1.417308  0.022692  0.180871       434    S5527_ST   S507_ST   
278   0.021441   2.010591  0.002263  0.070591       434    S5527_ST  S5527_ML   
21    0.011745   2.169024  0.000089  0.030282       434  S507_MLexp   S507_ML   

    Coregulated    source  
195          Up  REACTOME  
278          Up  REACTOME  
21           Up  REACTOME  
***
R-SPO-8964539
{'O53203', 'P9WN37'}
3
     p.geomean  sta

In [ ]:
summary.describe("mtu00280")


     p.geomean  stat.mean     p.val     q.val  set.size     Exposed   Control  \
702   0.063392   1.525081  0.015654  0.040754       260    S5527_ST  S5527_ML   
509   0.047029   1.490610  0.005026  0.018074       260  S507_MLexp   S507_ML   

    Coregulated   source  
702          Up  METACYC  
509          Up  METACYC  
***
PWY-7210
{'O53872'}
2
     p.geomean  stat.mean     p.val     q.val  set.size     Exposed   Control  \
880   0.103307   1.256594  0.037914  0.078926       367    S5527_ST  S5527_ML   
487   0.050624   1.526608  0.004152  0.015596       367  S507_MLexp   S507_ML   

    Coregulated   source  
880          Up  METACYC  
487          Up  METACYC  
***
PWY-7205
{'O53872'}
2
     p.geomean  stat.mean     p.val     q.val  set.size     Exposed   Control  \
464   0.031974   1.852758  0.004464  0.016382       288    S5527_ST  S5527_ML   
336   0.028435   1.737429  0.001350  0.007348       288  S507_MLexp   S507_ML   

    Coregulated   source  
464          Up  METACYC  

In [ ]:
protein='P96890' # accA3
peptide_filt= summary.diff_peptides_combined[summary.diff_peptides_combined['BLASTP'] == protein]['Row.names'].unique()
tss_filt= tss_sample_any[tss_sample_any['BLASTP'] == protein]['PeptideSequence'].unique()
combined_filt = list(tss_filt)+ list(peptide_filt)
combined_peptide_annotations[combined_peptide_annotations['PeptideSequence'].apply(lambda x : x in combined_filt) ][filt_cols].drop_duplicates()

In [ ]:
protein='O53422' # fadA3
peptide_filt= summary.diff_peptides_combined[summary.diff_peptides_combined['BLASTP'] == protein]['Row.names'].unique()
tss_filt= tss_sample_any[tss_sample_any['BLASTP'] == protein]['PeptideSequence'].unique()
combined_filt = list(tss_filt)+ list(peptide_filt)
combined_peptide_annotations[combined_peptide_annotations['PeptideSequence'].apply(lambda x : x in combined_filt) ][filt_cols].drop_duplicates()

In [ ]:
protein='O53872' # fadB
peptide_filt= summary.diff_peptides_combined[summary.diff_peptides_combined['BLASTP'] == protein]['Row.names'].unique()
tss_filt= tss_sample_any[tss_sample_any['BLASTP'] == protein]['PeptideSequence'].unique()
combined_filt = list(tss_filt)+ list(peptide_filt)
combined_peptide_annotations[combined_peptide_annotations['PeptideSequence'].apply(lambda x : x in combined_filt) ][filt_cols].drop_duplicates()

In [ ]:
protein='P96414' # fadE4
peptide_filt= summary.diff_peptides_combined[summary.diff_peptides_combined['BLASTP'] == protein]['Row.names'].unique()
tss_filt= tss_sample_any[tss_sample_any['BLASTP'] == protein]['PeptideSequence'].unique()
combined_filt = list(tss_filt)+ list(peptide_filt)
combined_peptide_annotations[combined_peptide_annotations['PeptideSequence'].apply(lambda x : x in combined_filt) ][filt_cols].drop_duplicates()

In [ ]:
exclusive_tss[exclusive_tss['BLASTP'] == 'P96890']

In [ ]:
summary.describe("mtu00380")

In [ ]:
summary.describe("mtu00310")


***
PWY-4381
{'O53872', 'O53422'}
3
     p.geomean  stat.mean     p.val     q.val  set.size      Exposed  \
374   0.048345  -1.239841  0.040242  0.184606       358  S5527_MLexp   
406   0.024464   1.944015  0.003035  0.013676       358     S5527_ST   
319   0.034988   1.769859  0.001108  0.006350       358   S507_MLexp   

        Control Coregulated   source  
374  S507_MLexp        Down  METACYC  
406    S5527_ML          Up  METACYC  
319     S507_ML          Up  METACYC  
***
PWY-7909
{'O53872'}
2
     p.geomean  stat.mean     p.val     q.val  set.size     Exposed   Control  \
675   0.058338   1.561695  0.013735  0.037264       269    S5527_ST  S5527_ML   
536   0.049740   1.465013  0.005700  0.019460       269  S507_MLexp   S507_ML   

    Coregulated   source  
675          Up  METACYC  
536          Up  METACYC  
***
PWY-7346
{'O53872'}
2
     p.geomean  stat.mean     p.val     q.val  set.size     Exposed   Control  \
509   0.032077   1.852552  0.004564  0.016382       126    S

In [ ]:
summary.describe('mtu00360')

## 3.4.4. Central Carbon and Energy Metabolism

In [ ]:
summary.describe("mtu01200")

In [ ]:
summary.sig_res[summary.sig_res['RowName'] == 'PWY66-399' ]

In [ ]:
# only acetylated in hyper-virulent strain stationary phase
protein='Q79FJ2'
peptide_filt= summary.diff_peptides_combined[summary.diff_peptides_combined['BLASTP'] == protein]['Row.names'].unique()
tss_filt= tss_sample_any[tss_sample_any['BLASTP'] == protein]['PeptideSequence'].unique()
combined_filt = list(tss_filt)+ list(peptide_filt)
combined_peptide_annotations[combined_peptide_annotations['PeptideSequence'].apply(lambda x : x in combined_filt) ][filt_cols].drop_duplicates()

In [ ]:
summary.describe("mtu00010")

In [ ]:
# 2 alternative TSSs identified , in both stranis. The shorter proteoform is not identified in MLexp  or ST of the hyper-virulent strain, but is identified in the these two conditions in the hypo-virulent strains. 
# the longer isoform is exlusively acetylated in S5527_ML. 
protein='O07717'
peptide_filt= summary.diff_peptides_combined[summary.diff_peptides_combined['BLASTP'] == protein]['Row.names'].unique()
tss_filt= tss_sample_any[tss_sample_any['BLASTP'] == protein]['PeptideSequence'].unique()
combined_filt = list(tss_filt)+ list(peptide_filt)
combined_peptide_annotations[combined_peptide_annotations['PeptideSequence'].apply(lambda x : x in combined_filt) ][filt_cols].drop_duplicates()

In [ ]:
summary.describe("mtu00020")

In [ ]:
summary.describe("mtu00630")

In [ ]:
summary.describe("mtu00620")

In [ ]:
protein='P9WIH3'
peptide_filt= summary.diff_peptides_combined[summary.diff_peptides_combined['BLASTP'] == protein]['Row.names'].unique()
tss_filt= tss_sample_any[tss_sample_any['BLASTP'] == protein]['PeptideSequence'].unique()
combined_filt = list(tss_filt)+ list(peptide_filt)
combined_peptide_annotations[combined_peptide_annotations['PeptideSequence'].apply(lambda x : x in combined_filt) ][filt_cols].drop_duplicates()

In [ ]:
protein='P9WIS9'
peptide_filt= summary.diff_peptides_combined[summary.diff_peptides_combined['BLASTP'] == protein]['Row.names'].unique()
tss_filt= tss_sample_any[tss_sample_any['BLASTP'] == protein]['PeptideSequence'].unique()
combined_filt = list(tss_filt)+ list(peptide_filt)
combined_peptide_annotations[combined_peptide_annotations['PeptideSequence'].apply(lambda x : x in combined_filt) ][filt_cols].drop_duplicates()

In [ ]:
protein='P96890'
peptide_filt= summary.diff_peptides_combined[summary.diff_peptides_combined['BLASTP'] == protein]['Row.names'].unique()
tss_filt= tss_sample_any[tss_sample_any['BLASTP'] == protein]['PeptideSequence'].unique()
combined_filt = list(tss_filt)+ list(peptide_filt)
combined_peptide_annotations[combined_peptide_annotations['PeptideSequence'].apply(lambda x : x in combined_filt) ][filt_cols].drop_duplicates()

In [ ]:
protein='O53422'
peptide_filt= summary.diff_peptides_combined[summary.diff_peptides_combined['BLASTP'] == protein]['Row.names'].unique()
tss_filt= tss_sample_any[tss_sample_any['BLASTP'] == protein]['PeptideSequence'].unique()
combined_filt = list(tss_filt)+ list(peptide_filt)
combined_peptide_annotations[combined_peptide_annotations['PeptideSequence'].apply(lambda x : x in combined_filt) ][filt_cols].drop_duplicates()

In [ ]:
def get_protein_summary(prot):
    res = summary.norm[summary.norm['Leading.Protein']==prot]['Leading.Protein.Kegg.Pathways'].apply(lambda x : x.split(';')).tolist()[0]
    sigs = []
    for i in res:
        if i in summary.sig_res['RowName'].tolist():
            sigs.append(i)

    #print(summary.kegg_summary.columns)    

    # filter the summary.kegg_summary by the index using sigs

    filtered_summary = summary.kegg_summary.loc[sigs]

    return filtered_summary

print(get_protein_summary('O53422'))
        

In [ ]:
#print(summary.norm[summary.norm['Leading Protein BLASTP'] == 'O53422'])
print(summary.norm)

### Oxidative Phosphorylation (mtu00190)

In [ ]:
summary.describe("mtu00190")

In [ ]:
protein='P9WP71'
peptide_filt= summary.diff_peptides_combined[summary.diff_peptides_combined['BLASTP'] == protein]['Row.names'].unique()
tss_filt= tss_sample_any[tss_sample_any['BLASTP'] == protein]['PeptideSequence'].unique()
combined_filt = list(tss_filt)+ list(peptide_filt)
combined_peptide_annotations[combined_peptide_annotations['PeptideSequence'].apply(lambda x : x in combined_filt) ][filt_cols].drop_duplicates()

### Propanoate metabolism

In [ ]:
summary.describe("mtu00640")

In [ ]:
protein='O53166'
peptide_filt= summary.diff_peptides_combined[summary.diff_peptides_combined['BLASTP'] == protein]['Row.names'].unique()
tss_filt= tss_sample_any[tss_sample_any['BLASTP'] == protein]['PeptideSequence'].unique()
combined_filt = list(tss_filt)+ list(peptide_filt)
combined_peptide_annotations[combined_peptide_annotations['PeptideSequence'].apply(lambda x : x in combined_filt) ][filt_cols].drop_duplicates()

In [ ]:
exclusive_tss[exclusive_tss['BLASTP'] == 'O53166']

In [ ]:
protein='O53872'
peptide_filt= summary.diff_peptides_combined[summary.diff_peptides_combined['BLASTP'] == protein]['Row.names'].unique()
tss_filt= tss_sample_any[tss_sample_any['BLASTP'] == protein]['PeptideSequence'].unique()
combined_filt = list(tss_filt)+ list(peptide_filt)
print(get_protein_summary(protein))

combined_peptide_annotations[combined_peptide_annotations['PeptideSequence'].apply(lambda x : x in combined_filt) ][filt_cols].drop_duplicates()

In [ ]:
protein='P96890'
peptide_filt= summary.diff_peptides_combined[summary.diff_peptides_combined['BLASTP'] == protein]['Row.names'].unique()
tss_filt= tss_sample_any[tss_sample_any['BLASTP'] == protein]['PeptideSequence'].unique()
combined_filt = list(tss_filt)+ list(peptide_filt)
combined_peptide_annotations[combined_peptide_annotations['PeptideSequence'].apply(lambda x : x in combined_filt) ][filt_cols].drop_duplicates()

In [ ]:
print(get_protein_summary('P96890'))


In [ ]:
exclusive_tss[exclusive_tss['BLASTP'] == 'P96890']

In [ ]:
summary.describe("mtu00650")

In [ ]:
summary.describe("mtu00362")

## 3.4.5 Lipid and Fatty Acid Pathways

In [ ]:
summary.describe("mtu01212")

In [ ]:
protein='O53872' # fadB
peptide_filt= summary.diff_peptides_combined[summary.diff_peptides_combined['BLASTP'] == protein]['Row.names'].unique()
tss_filt= tss_sample_any[tss_sample_any['BLASTP'] == protein]['PeptideSequence'].unique()
combined_filt = list(tss_filt)+ list(peptide_filt)
combined_peptide_annotations[combined_peptide_annotations['PeptideSequence'].apply(lambda x : x in combined_filt) ][filt_cols].drop_duplicates()

In [ ]:
protein='P95029' # fas
peptide_filt= summary.diff_peptides_combined[summary.diff_peptides_combined['BLASTP'] == protein]['Row.names'].unique()
tss_filt= tss_sample_any[tss_sample_any['BLASTP'] == protein]['PeptideSequence'].unique()
combined_filt = list(tss_filt)+ list(peptide_filt)
combined_peptide_annotations[combined_peptide_annotations['PeptideSequence'].apply(lambda x : x in combined_filt) ][filt_cols].drop_duplicates()

In [ ]:
protein='P96414' # fadE4
peptide_filt= summary.diff_peptides_combined[summary.diff_peptides_combined['BLASTP'] == protein]['Row.names'].unique()
tss_filt= tss_sample_any[tss_sample_any['BLASTP'] == protein]['PeptideSequence'].unique()
combined_filt = list(tss_filt)+ list(peptide_filt)
combined_peptide_annotations[combined_peptide_annotations['PeptideSequence'].apply(lambda x : x in combined_filt) ][filt_cols].drop_duplicates()

In [ ]:
summary.sig_res[summary.sig_res['RowName'] == 'PWY-7895' ]

In [ ]:
protein="P96404"
peptide_filt= summary.diff_peptides_combined[summary.diff_peptides_combined['BLASTP'] == protein]['Row.names'].unique()
tss_filt= tss_sample_any[tss_sample_any['BLASTP'] == protein]['PeptideSequence'].unique()
combined_filt = list(tss_filt)+ list(peptide_filt)
combined_peptide_annotations[combined_peptide_annotations['PeptideSequence'].apply(lambda x : x in combined_filt) ][filt_cols].drop_duplicates()

In [ ]:
summary.sig_res[summary.sig_res['RowName'] == 'PWY-7744' ]

In [ ]:
protein="P96414" # fadE4
peptide_filt= summary.diff_peptides_combined[summary.diff_peptides_combined['BLASTP'] == protein]['Row.names'].unique()
tss_filt= tss_sample_any[tss_sample_any['BLASTP'] == protein]['PeptideSequence'].unique()
combined_filt = list(tss_filt)+ list(peptide_filt)
combined_peptide_annotations[combined_peptide_annotations['PeptideSequence'].apply(lambda x : x in combined_filt) ][filt_cols].drop_duplicates()

In [ ]:
summary.sig_res[summary.sig_res['RowName'] == 'PWY-7744' ]

In [ ]:
protein='I6Y231'
peptide_filt= summary.diff_peptides_combined[summary.diff_peptides_combined['BLASTP'] == protein]['Row.names'].unique()
tss_filt= tss_sample_any[tss_sample_any['BLASTP'] == protein]['PeptideSequence'].unique()
combined_filt = list(tss_filt)+ list(peptide_filt)
combined_peptide_annotations[combined_peptide_annotations['PeptideSequence'].apply(lambda x : x in combined_filt) ][filt_cols].drop_duplicates()

In [ ]:
summary.describe('mtu00071')

In [ ]:
summary.describe('mtu00074')

In [ ]:
protein='I6X8D2'
peptide_filt= summary.diff_peptides_combined[summary.diff_peptides_combined['BLASTP'] == protein]['Row.names'].unique()
tss_filt= tss_sample_any[tss_sample_any['BLASTP'] == protein]['PeptideSequence'].unique()
combined_filt = list(tss_filt)+ list(peptide_filt)
combined_peptide_annotations[combined_peptide_annotations['PeptideSequence'].apply(lambda x : x in combined_filt) ][filt_cols].drop_duplicates()

In [ ]:
exclusive_tss[exclusive_tss['BLASTP'] == 'I6X8D2']

In [ ]:
protein='O53580'
peptide_filt= summary.diff_peptides_combined[summary.diff_peptides_combined['BLASTP'] == protein]['Row.names'].unique()
tss_filt= tss_sample_any[tss_sample_any['BLASTP'] == protein]['PeptideSequence'].unique()
combined_filt = list(tss_filt)+ list(peptide_filt)
combined_peptide_annotations[combined_peptide_annotations['PeptideSequence'].apply(lambda x : x in combined_filt) ][filt_cols].drop_duplicates()

In [ ]:
exclusive_tss[exclusive_tss['BLASTP'] == 'O53580']

In [ ]:
protein='P9WQD9'
peptide_filt= summary.diff_peptides_combined[summary.diff_peptides_combined['BLASTP'] == protein]['Row.names'].unique()
tss_filt= tss_sample_any[tss_sample_any['BLASTP'] == protein]['PeptideSequence'].unique()
combined_filt = list(tss_filt)+ list(peptide_filt)
combined_peptide_annotations[combined_peptide_annotations['PeptideSequence'].apply(lambda x : x in combined_filt) ][filt_cols].drop_duplicates()

In [ ]:
protein='P9WQD7'
peptide_filt= summary.diff_peptides_combined[summary.diff_peptides_combined['BLASTP'] == protein]['Row.names'].unique()
tss_filt= tss_sample_any[tss_sample_any['BLASTP'] == protein]['PeptideSequence'].unique()
combined_filt = list(tss_filt)+ list(peptide_filt)
combined_peptide_annotations[combined_peptide_annotations['PeptideSequence'].apply(lambda x : x in combined_filt) ][filt_cols].drop_duplicates()

### 3.4.6. Cofactor Biosynthesis and Related Systems

In [ ]:
summary.describe('mtu01240')

In [ ]:
summary.describe('mtu00670')

In [ ]:
protein='P9WGV3'
peptide_filt= summary.diff_peptides_combined[summary.diff_peptides_combined['BLASTP'] == protein]['Row.names'].unique()
tss_filt= tss_sample_any[tss_sample_any['BLASTP'] == protein]['PeptideSequence'].unique()
combined_filt = list(tss_filt)+ list(peptide_filt)
combined_peptide_annotations[combined_peptide_annotations['PeptideSequence'].apply(lambda x : x in combined_filt) ][filt_cols].drop_duplicates()

In [ ]:
term_prots = self.annotation2protein[newterm]

In [ ]:
protein='P9WGI9'
peptide_filt= summary.diff_peptides_combined[summary.diff_peptides_combined['BLASTP'] == protein]['Row.names'].unique()
tss_filt= tss_sample_any[tss_sample_any['BLASTP'] == protein]['PeptideSequence'].unique()
combined_filt = list(tss_filt)+  list(peptide_filt)
_ = combined_peptide_annotations[combined_peptide_annotations['PeptideSequence'].apply(lambda x : x in combined_filt) ][filt_cols + ['AnnotationMessage']].drop_duplicates()
_

In [ ]:
summary.describe('mtu04122')

## 3.4.7. Nucleotide and Nitrogen Metabolism

In [ ]:
summary.describe('mtu00230')

In [ ]:
protein='P9WKE3'
peptide_filt= summary.diff_peptides_combined[summary.diff_peptides_combined['BLASTP'] == protein]['Row.names'].unique()
tss_filt= tss_sample_any[tss_sample_any['BLASTP'] == protein]['PeptideSequence'].unique()
combined_filt = list(tss_filt)+ list(peptide_filt)
combined_peptide_annotations[combined_peptide_annotations['PeptideSequence'].apply(lambda x : x in combined_filt) ][filt_cols].drop_duplicates()

In [ ]:
protein='P9WMS7'
peptide_filt= summary.diff_peptides_combined[summary.diff_peptides_combined['BLASTP'] == protein]['Row.names'].unique()
tss_filt= tss_sample_any[tss_sample_any['BLASTP'] == protein]['PeptideSequence'].unique()
combined_filt = list(tss_filt)+ list(peptide_filt)
combined_peptide_annotations[combined_peptide_annotations['PeptideSequence'].apply(lambda x : x in combined_filt) ][filt_cols].drop_duplicates()

In [ ]:
summary.norm[summary.norm['Leading.Protein'] =='P9WMS7']

In [ ]:
protein='P9WHQ9'
peptide_filt= summary.diff_peptides_combined[summary.diff_peptides_combined['BLASTP'] == protein]['Row.names'].unique()
tss_filt= tss_sample_any[tss_sample_any['BLASTP'] == protein]['PeptideSequence'].unique()
combined_filt = list(tss_filt)+ list(peptide_filt)
combined_peptide_annotations[combined_peptide_annotations['PeptideSequence'].apply(lambda x : x in combined_filt) ][filt_cols].drop_duplicates()

In [ ]:
summary.describe("mtu00910")

In [ ]:
protein='P9WN37'
peptide_filt= summary.diff_peptides_combined[summary.diff_peptides_combined['BLASTP'] == protein]['Row.names'].unique()
tss_filt= tss_sample_any[tss_sample_any['BLASTP'] == protein]['PeptideSequence'].unique()
combined_filt = list(tss_filt)+ list(peptide_filt)
combined_peptide_annotations[combined_peptide_annotations['PeptideSequence'].apply(lambda x : x in combined_filt) ][filt_cols].drop_duplicates()

In [ ]:
protein='O53203'
peptide_filt= summary.diff_peptides_combined[summary.diff_peptides_combined['BLASTP'] == protein]['Row.names'].unique()
tss_filt= tss_sample_any[tss_sample_any['BLASTP'] == protein]['PeptideSequence'].unique()
combined_filt = list(tss_filt)+ list(peptide_filt)
combined_peptide_annotations[combined_peptide_annotations['PeptideSequence'].apply(lambda x : x in combined_filt) ][filt_cols].drop_duplicates()

In [ ]:
summary.describe("mtu00240")

In [ ]:
protein='P9WFS1'
peptide_filt= summary.diff_peptides_combined[summary.diff_peptides_combined['BLASTP'] == protein]['Row.names'].unique()
tss_filt= tss_sample_any[tss_sample_any['BLASTP'] == protein]['PeptideSequence'].unique()
combined_filt = list(tss_filt)+ list(peptide_filt)
combined_peptide_annotations[combined_peptide_annotations['PeptideSequence'].apply(lambda x : x in combined_filt) ][filt_cols].drop_duplicates()

In [ ]:
protein='P9WHL3'
peptide_filt= summary.diff_peptides_combined[summary.diff_peptides_combined['BLASTP'] == protein]['Row.names'].unique()
tss_filt= tss_sample_any[tss_sample_any['BLASTP'] == protein]['PeptideSequence'].unique()
combined_filt = list(tss_filt)+ list(peptide_filt)
combined_peptide_annotations[combined_peptide_annotations['PeptideSequence'].apply(lambda x : x in combined_filt) ][filt_cols].drop_duplicates()

### 3.4.8. Stress-Specific Pathways and Transport

In [ ]:
summary.describe('mtu00680')

In [ ]:
protein='P9WP79'
peptide_filt= summary.diff_peptides_combined[summary.diff_peptides_combined['BLASTP'] == protein]['Row.names'].unique()
tss_filt= tss_sample_any[tss_sample_any['BLASTP'] == protein]['PeptideSequence'].unique()
combined_filt = list(tss_filt)+ list(peptide_filt)
combined_peptide_annotations[combined_peptide_annotations['PeptideSequence'].apply(lambda x : x in combined_filt) ][filt_cols].drop_duplicates()

In [ ]:
summary.describe('mtu00572')

In [ ]:
protein='O53582'
peptide_filt= summary.diff_peptides_combined[summary.diff_peptides_combined['BLASTP'] == protein]['Row.names'].unique()
tss_filt= tss_sample_any[tss_sample_any['BLASTP'] == protein]['PeptideSequence'].unique()
combined_filt = list(tss_filt)+ list(peptide_filt)
combined_peptide_annotations[combined_peptide_annotations['PeptideSequence'].apply(lambda x : x in combined_filt) ][filt_cols].drop_duplicates()


In [ ]:
summary.describe("mtu01053")

In [ ]:
protein='O05819'
peptide_filt= summary.diff_peptides_combined[summary.diff_peptides_combined['BLASTP'] == protein]['Row.names'].unique()
tss_filt= tss_sample_any[tss_sample_any['BLASTP'] == protein]['PeptideSequence'].unique()
combined_filt = list(tss_filt)+ list(peptide_filt)
combined_peptide_annotations[combined_peptide_annotations['PeptideSequence'].apply(lambda x : x in combined_filt) ][filt_cols].drop_duplicates()

In [ ]:
protein='O33336'
peptide_filt= summary.diff_peptides_combined[summary.diff_peptides_combined['BLASTP'] == protein]['Row.names'].unique()
tss_filt= tss_sample_any[tss_sample_any['BLASTP'] == protein]['PeptideSequence'].unique()
combined_filt = list(tss_filt)+ list(peptide_filt)
combined_peptide_annotations[combined_peptide_annotations['PeptideSequence'].apply(lambda x : x in combined_filt) ][filt_cols].drop_duplicates()

In [ ]:
combined_peptide_annotations[combined_peptide_annotations['PeptideSequence'].apply(lambda x : x in combined_filt) ].drop_duplicates()

In [ ]:
summary.describe("mtu03070")

In [ ]:
protein='P9WGN3' # secY
peptide_filt= summary.diff_peptides_combined[summary.diff_peptides_combined['BLASTP'] == protein]['Row.names'].unique()
tss_filt= tss_sample_any[tss_sample_any['BLASTP'] == protein]['PeptideSequence'].unique()
combined_filt = list(tss_filt)+ list(peptide_filt)
combined_peptide_annotations[combined_peptide_annotations['PeptideSequence'].apply(lambda x : x in combined_filt) ][filt_cols].drop_duplicates()

In [ ]:
protein='P9WGP3' # secA2
peptide_filt= summary.diff_peptides_combined[summary.diff_peptides_combined['BLASTP'] == protein]['Row.names'].unique()
tss_filt= tss_sample_any[tss_sample_any['BLASTP'] == protein]['PeptideSequence'].unique()
combined_filt = list(tss_filt)+ list(peptide_filt)
combined_peptide_annotations[combined_peptide_annotations['PeptideSequence'].apply(lambda x : x in combined_filt) ][filt_cols].drop_duplicates()

In [ ]:
protein='P9WIT5'
peptide_filt= summary.diff_peptides_combined[summary.diff_peptides_combined['BLASTP'] == protein]['Row.names'].unique()
tss_filt= tss_sample_any[tss_sample_any['BLASTP'] == protein]['PeptideSequence'].unique()
combined_filt = list(tss_filt)+ list(peptide_filt)
combined_peptide_annotations[combined_peptide_annotations['PeptideSequence'].apply(lambda x : x in combined_filt) ][filt_cols].drop_duplicates()

In [ ]:
summary.describe("mtu02010")

In [ ]:
protein='O06138'
peptide_filt= summary.diff_peptides_combined[summary.diff_peptides_combined['BLASTP'] == protein]['Row.names'].unique()
tss_filt= tss_sample_any[tss_sample_any['BLASTP'] == protein]['PeptideSequence'].unique()
combined_filt = list(tss_filt)+ list(peptide_filt)
combined_peptide_annotations[combined_peptide_annotations['PeptideSequence'].apply(lambda x : x in combined_filt) ][filt_cols].drop_duplicates()

In [ ]:
protein='P9WG19'
peptide_filt= summary.diff_peptides_combined[summary.diff_peptides_combined['BLASTP'] == protein]['Row.names'].unique()
tss_filt= tss_sample_any[tss_sample_any['BLASTP'] == protein]['PeptideSequence'].unique()
combined_filt = list(tss_filt)+ list(peptide_filt)
combined_peptide_annotations[combined_peptide_annotations['PeptideSequence'].apply(lambda x : x in combined_filt) ][filt_cols].drop_duplicates()

In [ ]:
protein='P9WGU5'
peptide_filt= summary.diff_peptides_combined[summary.diff_peptides_combined['BLASTP'] == protein]['Row.names'].unique()
tss_filt= tss_sample_any[tss_sample_any['BLASTP'] == protein]['PeptideSequence'].unique()
combined_filt = list(tss_filt)+ list(peptide_filt)
combined_peptide_annotations[combined_peptide_annotations['PeptideSequence'].apply(lambda x : x in combined_filt) ][filt_cols].drop_duplicates()

In [ ]:
protein='P9WQL5'
peptide_filt= summary.diff_peptides_combined[summary.diff_peptides_combined['BLASTP'] == protein]['Row.names'].unique()
tss_filt= tss_sample_any[tss_sample_any['BLASTP'] == protein]['PeptideSequence'].unique()
combined_filt = list(tss_filt)+ list(peptide_filt)
combined_peptide_annotations[combined_peptide_annotations['PeptideSequence'].apply(lambda x : x in combined_filt) ][filt_cols].drop_duplicates()

In [ ]:
combined_peptide_annotations[combined_peptide_annotations['PeptideSequence'].apply(lambda x : x in combined_filt) ].drop_duplicates()

In [ ]:
summary.describe("mtu01120")

In [ ]:
summary.describe('mtu01210')

In [ ]:
protein='P9WIS5'
peptide_filt= summary.diff_peptides_combined[summary.diff_peptides_combined['BLASTP'] == protein]['Row.names'].unique()
tss_filt= tss_sample_any[tss_sample_any['BLASTP'] == protein]['PeptideSequence'].unique()
combined_filt = list(tss_filt)+ list(peptide_filt)
combined_peptide_annotations[combined_peptide_annotations['PeptideSequence'].apply(lambda x : x in combined_filt) ][filt_cols].drop_duplicates()

In [ ]:
summary.describe("MT0172-MT0187")

In [ ]:
protein='O07420'
peptide_filt= summary.diff_peptides_combined[summary.diff_peptides_combined['BLASTP'] == protein]['Row.names'].unique()
tss_filt= tss_sample_any[tss_sample_any['BLASTP'] == protein]['PeptideSequence'].unique()
combined_filt = list(tss_filt)+ list(peptide_filt)
combined_peptide_annotations[combined_peptide_annotations['PeptideSequence'].apply(lambda x : x in combined_filt) ][filt_cols].drop_duplicates()

## 3.4.9 Stationary-Specific Pathways

In [ ]:
summary.describe('mtu00983')

In [ ]:
protein='P9WMR7'
peptide_filt= summary.diff_peptides_combined[summary.diff_peptides_combined['BLASTP'] == protein]['Row.names'].unique()
tss_filt= tss_sample_any[tss_sample_any['BLASTP'] == protein]['PeptideSequence'].unique()
combined_filt = list(tss_filt)+ list(peptide_filt)
combined_peptide_annotations[combined_peptide_annotations['PeptideSequence'].apply(lambda x : x in combined_filt) ][filt_cols].drop_duplicates()

In [ ]:
summary.describe("mtu00710")

In [ ]:
summary.describe("mtu00970")

In [ ]:
summary.describe("MT3233–MT3246")

In [ ]:
summary.describe("MT3233–MT3246")

In [ ]:
combined_peptide_annotations[combined_peptide_annotations['PeptideSequence'].apply(lambda x : x in combined_filt) ]['ORF_id'].drop_duplicates().tolist()

In [ ]:
def get_var_length(c1,c2):
    nuc_len = c2+1 - c1
    amino_len=  nuc_len/3
    return amino_len
get_var_length(40035,40649)

In [ ]:
combined_peptide_annotations[combined_peptide_annotations['PeptideSequence'] == 'RYSDSYHTTGRWQPRASTEGFPMGVSIEVNGLTK']['ORF_id'].tolist()

In [ ]:
ev[ev['Sequence'] == 'MPGYHIEDQR'][['Experiment','Intensity','MS/MS Count','Intensity']]

In [ ]:
p = pd.read_csv('data/txt/peptides.txt',sep='\t')

In [ ]:
icols = [ i for i in p.columns if i.startswith("Intensity ") ] 
p[p['Sequence'] == 'MPGYHIEDQR'][icols]

## 	Mycolic acid biosynthesis (mtu00074)

In [ ]:
summary.describe('mtu00074')

In [ ]:
# 3-oxoacyl-[acyl-carrier-protein] synthase 2, kasB
tss_sample_any[tss_sample_any['BLASTP']=='P9WQD7'][filt_cols]

In [ ]:
# Biotin-dependent acyl-coenzyme A carboxylase alpha3 subunit, accA3
tss_sample_any[tss_sample_any['BLASTP']=='P96890'][filt_cols]

In [ ]:
# Probable fatty acid synthase Fas (Fatty acid synthetase)
tss_sample_any[tss_sample_any['BLASTP']=='P95029'][filt_cols]

In [ ]:
# Long-chain-fatty-acid--AMP ligase FadD32
tss_sample_any[tss_sample_any['BLASTP']=='O53580'][filt_cols]

In [ ]:
# 4'-phosphopantetheinyl transferase PptT, pptT
tss_sample_any[tss_sample_any['BLASTP']=='O33336'][filt_cols]

In [ ]:
# Polyketide synthase Pks13
tss_sample_any[tss_sample_any['BLASTP']=='I6X8D2'][filt_cols]

In [ ]:
# Cyclopropane mycolic acid synthase MmaA2
acetyl_sample_any[acetyl_sample_any['BLASTP'] == 'Q79FX6'][acetyl_filt_cols]

In [ ]:
# UPF0336 protein Rv0504c
acetyl_sample_any[acetyl_sample_any['BLASTP'] == 'P9WFK3'][acetyl_filt_cols]

In [ ]:
# Cyclopropane mycolic acid synthase 3, pcaA
acetyl_sample_any[acetyl_sample_any['BLASTP'] == 'P9WPB3'][acetyl_filt_cols]

In [ ]:
# Cyclopropane mycolic acid synthase 2, cmaA2
acetyl_sample_any[acetyl_sample_any['BLASTP'] == 'P9WPB5'][acetyl_filt_cols]

In [ ]:
# 3-oxoacyl-[acyl-carrier-protein] synthase 1, kasA
acetyl_sample_any[acetyl_sample_any['BLASTP'] == 'P9WQD9'][acetyl_filt_cols]

In [ ]:
# Polyketide synthase Pks13, pks13
acetyl_sample_any[acetyl_sample_any['BLASTP'] == 'I6X8D2'][acetyl_filt_cols]

In [ ]:
summary.describe('mtu03010')

In [ ]:
# note - make sure to exlue kegg that are same intra strain comps

In [ ]:
print(len(summary.annotation2protein['IPR036689: ESAT-6-like superfamily']))

In [ ]:
summary.pathway_weight
sorted_weights= sorted(summary.pathway_weight.items(), key=lambda x: x[1], reverse=True)

In [ ]:
sorted_weights

In [ ]:
summary.norm[summary.norm['icds'] == '+']['X_ipr.term.union'].tolist()[2]